In [56]:
!pip freeze > requirements.txt
!py -m pip install -r requirements.txt
from fuzzywuzzy import fuzz
from fuzzywuzzy import process
import json
from tqdm import tqdm
import pymorphy2

Processing c:\home\ktietz\src\ci\alabaster_1611921544520\work


ERROR: Could not install packages due to an OSError: [Errno 2] No such file or directory: 'C:\\home\\ktietz\\src\\ci\\alabaster_1611921544520\\work'

You should consider upgrading via the 'C:\Users\fktrc\AppData\Local\Programs\Python\Python39\python.exe -m pip install --upgrade pip' command.


In [57]:
#Введите путь к .json
path = input()

In [58]:
with open(path, 'r', encoding='utf-8') as file:
    sentences = json.load(file)
sentences = [elem['text'] for elem in sentences]
sentences = [elem.lower() for elem in sentences]

In [59]:
verb_set = set()
for sentence in sentences:
    for word in sentence.split():
        parsed_word = morph.parse(word)[0]
        if parsed_word.tag.POS in ('VERB', 'INFN'):
            verb_set.add(parsed_word.normal_form)


In [61]:
import pymorphy2
import string

# Создайте экземпляр класса MorphAnalyzer для морфологического анализа
morph = pymorphy2.MorphAnalyzer()

# Функция для лемматизации предложения
def lemmatize_sentence(sentence):
    words = sentence.split()
    lemmas = [morph.parse(word)[0].normal_form for word in words]
    return lemmas

# Функция для сравнения двух предложений
def compare_sentences(lemmas1, lemmas2):
    common_words = set(lemmas1) & set(lemmas2)
    similarity = len(common_words) / len(set(lemmas1 + lemmas2))
    return similarity

def remove_punctuation(sentence):
    translator = str.maketrans('', '', string.punctuation)
    sentence = sentence.translate(translator)
    return sentence
sentences = [remove_punctuation(sentence) for sentence in sentences]

def replace_pronouns(sentence):
    words = sentence.split()
    for i, word in enumerate(words):
        parsed_word = morph.parse(word)[0]
        if 'NPRO' in parsed_word.tag:
            words[i] = '<PRONOUN>'
        
    return ' '.join(words)

similarity_matrix = {}

def levenshtein_distance(first_word, second_word):
    if len(first_word) < len(second_word):
        return levenshtein_distance(second_word, first_word)

    if len(second_word) == 0:
        return len(first_word)

    previous_row = list(range(len(second_word) + 1))

    for i, c1 in enumerate(first_word):
        current_row = [i + 1]

        for j, c2 in enumerate(second_word):
            # Calculate insertions, deletions and substitutions
            insertions = previous_row[j + 1] + 1
            deletions = current_row[j] + 1
            substitutions = previous_row[j] + (c1 != c2)

            # Get the minimum to append to the current row
            current_row.append(min(insertions, deletions, substitutions))

        # Store the previous row
        previous_row = current_row

    # Returns the last element (distance)
    return previous_row[-1]

def check_lev(s1, s2):
    if len(s1) > 5 and levenshtein_distance(s1, s2) <= 0:
        s1 = s2


# Сравните все пары предложений в датасете
for i in tqdm(range(len(sentences))):
    for j in range(i+1, len(sentences)):
        sentence1 = sentences[i]
        sentence2 = sentences[j]
        sentence1 = replace_pronouns(sentence1)
        sentence2 = replace_pronouns(sentence2)
        parsed_words = [morph.parse(word)[0].word  for word in sentence1.split() if morph.parse(word)[0].tag.POS in ('VERB','INFN')]
        parsed_words2 = [morph.parse(word)[0].word  for word in sentence2.split() if morph.parse(word)[0].tag.POS in ('VERB','INFN')]
        for word1 in set(parsed_words):
            for word2 in set(parsed_words2):
                check_lev(word1, word2)
        if set(parsed_words2) != set(parsed_words):
            lemmas1 = lemmatize_sentence(sentence1)
            lemmas2 = lemmatize_sentence(sentence2)
            similarity = compare_sentences(lemmas1, lemmas2)
            similarity_matrix[(i, j)] = similarity - 0.2
        else:
            lemmas1 = lemmatize_sentence(sentence1)
            lemmas2 = lemmatize_sentence(sentence2)
            similarity = compare_sentences(lemmas1, lemmas2)

            # Сохраните сходство в словаре
            similarity_matrix[(i, j)] = similarity
            

# Выведите результаты сходства между парами предложений
for (i, j), similarity in similarity_matrix.items():
    print(f"Сходство между предложением {i + 1} и предложением {j + 1}: {similarity}")


100%|██████████| 412/412 [06:35<00:00,  1.04it/s]


Сходство между предложением 1 и предложением 2: -0.07500000000000001
Сходство между предложением 1 и предложением 3: -0.07500000000000001
Сходство между предложением 1 и предложением 4: -0.1
Сходство между предложением 1 и предложением 5: -0.07500000000000001
Сходство между предложением 1 и предложением 6: -0.1
Сходство между предложением 1 и предложением 7: -0.0888888888888889
Сходство между предложением 1 и предложением 8: -0.2
Сходство между предложением 1 и предложением 9: -0.2
Сходство между предложением 1 и предложением 10: -0.07500000000000001
Сходство между предложением 1 и предложением 11: -0.05714285714285716
Сходство между предложением 1 и предложением 12: -0.05714285714285716
Сходство между предложением 1 и предложением 13: -0.1
Сходство между предложением 1 и предложением 14: -0.05714285714285716
Сходство между предложением 1 и предложением 15: -0.07500000000000001
Сходство между предложением 1 и предложением 16: -0.0888888888888889
Сходство между предложением 1 и предложе

In [62]:
sim = [(i, j) for (i, j), similarity in similarity_matrix.items() if similarity>0.5]

In [63]:
sim

[(1, 4),
 (1, 14),
 (1, 69),
 (1, 149),
 (1, 171),
 (1, 233),
 (2, 265),
 (3, 12),
 (4, 14),
 (4, 69),
 (4, 149),
 (4, 171),
 (4, 233),
 (6, 270),
 (9, 80),
 (9, 86),
 (9, 278),
 (9, 292),
 (13, 100),
 (13, 256),
 (13, 281),
 (14, 69),
 (14, 149),
 (14, 171),
 (14, 233),
 (16, 350),
 (18, 70),
 (18, 396),
 (19, 393),
 (21, 342),
 (23, 139),
 (24, 85),
 (25, 263),
 (28, 142),
 (28, 217),
 (28, 225),
 (28, 290),
 (28, 330),
 (28, 358),
 (28, 383),
 (29, 77),
 (29, 122),
 (29, 362),
 (31, 300),
 (32, 296),
 (32, 319),
 (33, 266),
 (34, 253),
 (35, 301),
 (35, 401),
 (36, 195),
 (37, 352),
 (39, 209),
 (40, 144),
 (43, 407),
 (45, 199),
 (47, 284),
 (48, 267),
 (49, 311),
 (52, 118),
 (53, 271),
 (55, 172),
 (56, 62),
 (57, 74),
 (58, 385),
 (60, 120),
 (61, 244),
 (63, 117),
 (64, 379),
 (65, 106),
 (66, 110),
 (67, 79),
 (69, 149),
 (69, 171),
 (69, 233),
 (70, 396),
 (73, 96),
 (77, 122),
 (77, 362),
 (78, 275),
 (78, 336),
 (80, 86),
 (80, 278),
 (80, 292),
 (81, 113),
 (82, 105),
 (83

In [65]:
def extract(s: str, arr: list[str], sim: list[(int, int)]):
    res = []
    for cop in sim:
        if s == sentences[cop[0]]:
            res.append(sentences[cop[1]])
    res = sorted(res, reverse=True)
    return res
result = {}
for i in range(len(sentences)):
    result[sentences[i]] = extract(sentences[i], sentences[:i] + sentences[i + 1:], sim)

with open('result2.json', 'w') as file:
    json.dump(result, file, indent=4, ensure_ascii=False)
